In [25]:
#LSTM GENERATOR
import numpy as np
import gzip
import nltk
from random import randint
import torch
import gzip
import numpy as np
from random import randint
import torch.utils.data as data_utils
import torch
import torch.autograd as autograd
import torch.nn.functional as F
print "here"
import torch.nn as nn
import torch.utils.data as data
import torch.optim as optim
from torch.autograd import Variable
from sklearn.metrics.pairwise import cosine_similarity
from numpy import linalg as LA
import time

here


In [40]:
def make_lookup_table(filename):
    lookup={}
    text_token_list=convert_to_list(filename)
    for token in text_token_list:
        lookup[token[0]] = {'title':token[1],'question':token[2]}
    return lookup
def convert_to_list(filename, is_android = False):
    if filename.endswith('gz'):
        with gzip.open(filename,'r')as f:
            text_tokens = f.readlines()
    else:
        with open(filename, 'r') as f:
            text_tokens = f.readlines()
    
    text_tokens = [token.replace('\n','').split('\t') for token in text_tokens]
    if is_android:
        text_tokens = [token[0].split(' ') for token in text_tokens]
    else:
        text_tokens = [[token[0], token[1].split(' '), token[2].split(' ')] for token in text_tokens]
                   
    return text_tokens
def convert_to_samples_android(pos_filename, neg_filename):
    pos_list = convert_to_list(pos_filename, is_android = True)
    neg_list = convert_to_list(neg_filename, is_android = True)

    target_id_to_list_of_negative_ids = {}
    for id_pair in neg_list:
        target_id, negative_id = id_pair
        if target_id in target_id_to_list_of_negative_ids:
            target_id_to_list_of_negative_ids[target_id].append(negative_id)
        else:
            target_id_to_list_of_negative_ids[target_id] = [negative_id]
    new_samples = []
    for id_pair in pos_list:
        target_id, positive_id = id_pair
        negative_ids = target_id_to_list_of_negative_ids[target_id]
        new_sample = [target_id, positive_id, negative_ids]
        new_samples.append(new_sample)
    return new_samples
#takes  sample_ids of [[q1,p1,n1],[q2,p2,n2]....]
#outputs titles like [[q1_title, p1_title, n1_title],[q2_title,p2_title,n2_title]...]
def convert_sampleids_to_titles(sample_ids,lookup):
    #each sample_id [question_id, pos_id, [neg_ids]]
    #print type(sample_ids)==list, "first"
   
    titles = []
    for sample_id in sample_ids:
         #flatten list: [question_id, pos_id, [neg_ids]] --> [question_id, pos_id, neg_id1, neg_id2, ...]
        sample_id= sample_id[:2]+sample_id[2][:]
        #sample_id : question_id, similar_question_id, negative_question_id
        try:
            titles.append([[item.lower() for item in lookup[str(_)]['title']] for _ in sample_id])
        except:
            print "Lookup failed"
    return titles
def flatten_titles(titles):
    return ["" + word for q_list in titles for q in q_list for word in q]

In [ ]:
#ubuntu_text_tokenized_filename = 'askubuntu/text_tokenized.txt.gz'
android_text_tokenized_filename = 'Android/corpus.tsv.gz'
#ubuntu_data_lookup_table = make_lookup_table(ubuntu_text_tokenized_filename)
android_data_lookup_table = make_lookup_table(android_text_tokenized_filename)

android_dev_pos_filename = "Android/dev.pos.txt"
android_dev_neg_filename = "Android/dev.neg.txt"

android_test_pos_filename = "Android/test.pos.txt"
android_test_neg_filename = "Android/test.neg.txt"

android_dev_samples = convert_to_samples_android(android_dev_pos_filename, android_dev_neg_filename)
android_test_samples = convert_to_samples_android(android_test_pos_filename, android_test_neg_filename)

android_dev_titles_only = convert_sampleids_to_titles(android_dev_samples, android_data_lookup_table)
android_test_titles_only = convert_sampleids_to_titles(android_test_samples, android_data_lookup_table)

android_dev_words = flatten_titles(android_dev_titles_only)

In [ ]:
# android_dev_words_targets_and_positives_only = [word for q_list in android_dev_titles_only for q in q_list[:2] for word in q]
bigrams = nltk.bigrams(android_dev_words)
cfd = nltk.ConditionalFreqDist(bigrams)

In [29]:
N = 7
def generate_question(cfdist, target_question):
    generated_question = []
    word = target_question[0]
    generated_question.append(word)
    for idx in range(len(target_question)):
        try:
            word2 = select_random_word_from_top_n(cfdist[word], N)
            generated_question.append(word2)
        except:
            print word
        
    return generated_question

def select_random_word_from_top_n(freq_dist_dict, n):
    rand_idx = randint(0, n-1)
    top_n = sorted(freq_dist_dict.iteritems(), key = lambda x: x[1], reverse = True)[:n]
    return top_n[min(rand_idx, len(top_n)- 1)][0]

In [30]:
#-------------------------------------HELPER FUNCTIONS-------------------------------------#
NUM_NEGATIVE_SAMPLES=20

def N_random_values_in_list(full_list, N):
    x=0
    lower_bound  = 0
    upper_bound = len(full_list)-1
    sample_list=[]
    random_nums=[]
    while x < min(N,len(full_list)):
        random_num = randint(lower_bound, upper_bound) # inclusive range
        if random_num in random_nums:
            continue
        else:
            random_nums.append(random_num)
            x += 1
    return [full_list[i] for i in random_nums]

def convert_to_list(filename, is_android = False):
    if filename.endswith('gz'):
        with gzip.open(filename,'r')as f:
            text_tokens = f.readlines()
    else:
        with open(filename, 'r') as f:
            text_tokens = f.readlines()
    
    text_tokens = [token.replace('\n','').split('\t') for token in text_tokens]
    if is_android:
        text_tokens = [token[0].split(' ') for token in text_tokens]
    else:
        text_tokens = [[token[0], token[1].split(' '), token[2].split(' ')] for token in text_tokens]
                   
    return text_tokens

#Sample:question_id, similar_question_id, negative_question_id
def convert_to_samples(filename, is_dev_or_test = False):
    my_list=convert_to_list(filename)
    new_samples=[]
    for original_sample in my_list:
        if is_dev_or_test:
            new_samples.append([original_sample[0], similar, negative_samples])
        else:
            for similar in original_sample[1]:
                random_negative_samples = N_random_values_in_list(original_sample[2],NUM_NEGATIVE_SAMPLES)
                new_samples.append([original_sample[0], similar, random_negative_samples])# change this to include all negative 
                                                                                     # examples later
    return new_samples
def make_lookup_table_for_training_data(filename):
    lookup={}
    text_token_list=convert_to_list(filename)
    for token in text_token_list:
        lookup[token[0]] = {'title':token[1],'question':token[2]}
    return lookup
        
#takes  sample_ids of [[q1,p1,n1],[q2,p2,n2]....]
#outputs titles like [[q1_title, p1_title, n1_title],[q2_title,p2_title,n2_title]...]
def convert_sampleids_to_titles(sample_ids,lookup, is_dev_or_test = False):
    #each sample_id [question_id, pos_id, [neg_ids]]
    #print type(sample_ids)==list, "first"
   
    titles = []
   # print "sample_ids", sample_ids
    for sample_id in sample_ids:
        if is_dev_or_test:
            #omit similar questions, only needed for evaluation
            sample_id=[sample_id[0]]+sample_id[2][:]
         #flatten list: [question_id, pos_id, [neg_ids]] --> [question_id, pos_id, neg_id1, neg_id2, ...]
        else:
            sample_id= sample_id[:2]+sample_id[2][:]
        #sample_id : question_id, similar_question_id, negative_question_id
        #try:
        current=[]
        for identity in sample_id:
            try:
                current.append(lookup[str(identity)]['title'])
            except:
                print identity
        titles.append(current)
           # print type(sample_id)==list
        #except:
        #    print sample_id, "is sample id", type(sample_id)==list
    return titles
def remove_non_ascii(text):
    return ''.join([i if ord(i) < 128 else '' for i in text])

def extract_features(word):
    try:
        word=remove_non_ascii(word)
        word=word.encode('utf-8')
    except:
        print(word)
    return word_to_vec.get(word,[0.0 for i in range(300)])

def find_maximum_title_and_body_length(lookup_table):
    max_len_title = -1
    max_len_question = -1
    max_len_question_id = 0
    for key, dict_val in lookup_table.iteritems():
        len_title = len(dict_val['title'])
        len_question = len(dict_val['question'])
        if len_title > max_len_title:
             max_len_title = len_title
        if len_question > max_len_question:
            max_len_question = len_question
            max_len_question_id = key
    return max_len_title, max_len_question

def title_to_feature_matrix(title_word_list):
    feature_matrix = []
    for idx, word in enumerate(title_word_list):
        if idx == PARAMETER_MAX_TITLE_LENGTH:
            break
        else:
            word_features = extract_features(word)
            feature_matrix.append(word_features)
        
    #Pad the feature with zeros to ensure all inputs to the net have the same dimension
    feature_matrix += [[0] * NUM_FEATURES_PER_WORD] * (PARAMETER_MAX_TITLE_LENGTH - len(title_word_list))
    #print np.array(feature_matrix).T.shape
    return np.array(feature_matrix).T



#array is structured like a batch of features 50x200x38
def find_start_of_padding_for_batch(batch):
    vec_lengths_in_batch = []
    for batch_num in range(0, len(batch)):
        single_vec = batch[batch_num]
        length = find_start_of_padding_single_vec(single_vec) + 1
        vec_lengths_in_batch.append(length)
    return vec_lengths_in_batch

#batch = 200x38
def find_start_of_padding_single_vec(single_vec):
    for idx in range(len(single_vec[0])-1, -1, -1):
        if single_vec[0][idx] != 0.:
            return idx
    #if the whole sequence is 0s
    return 0
def create_mask(word_length):
    return np.array([[1. / word_length] * HIDDEN_SIZE] * word_length + [[0] * HIDDEN_SIZE] * (MAX_TITLE_LENGTH - word_length)).T
#-------------------------------------CREATE DATA BATCHER-------------------------------------#
# where samples[0] = 1 (target) + 1 (positive) + n (negative)
# 
def create_data_loader(samples, shuffle_data = True, is_test_or_dev = False):
    features = []
    for sample in samples:
        target_title = sample[0]
        positive_title = sample[1]
        negative_titles = sample[2:]

        target_features = title_to_feature_matrix(target_title)
        print target_features, "is taret features"
        positive_features = title_to_feature_matrix(positive_title)
        if len(negative_titles)==0:
            all_features=[target_features, positive_features]
        else:
            n_negative_features = [title_to_feature_matrix(negative_title) for negative_title in negative_titles]

            all_features = [target_features, positive_features] + n_negative_features
        #print all_features, "is all"
       # if is_test_or_dev:
       #     all_features = [target_features,]
        features.append(all_features)

            
    targets = torch.LongTensor(len(features)).zero_()
    dataset = data_utils.TensorDataset(torch.FloatTensor(features), targets)
    data_loader = data_utils.DataLoader(dataset, batch_size = BATCH_SIZE, shuffle = shuffle_data)
    return data_loader

In [31]:
# word_embeddings = 'askubuntu/vector/vectors_pruned.200.txt.gz'
# f = gzip.open(word_embeddings, 'r')
# wv_text = [ ]
# lines = f.readlines()
# for line in lines:
#     wv_text.append(line.strip())

# word_to_vec = {}

# for line in wv_text:
#     parts = line.split()
#     word = parts[0]
#     vector = np.array([float(v) for v in parts[1:]])
#     word_to_vec[word] = vector
# f.close()
start = time.time() # ---------------TAKES 7 MINUTES ---------------#
#-------------------------------------GENERATE EMBEDDINGS-------------------------------------#
import zipfile
# word_embeddings = 'askubuntu/vector/vectors_pruned.200.txt.gz'
word_embeddings = 'glove.txt'
start = time.time()
# f = gzip.open(word_embeddings, 'r')
f = open(word_embeddings, 'r')
wv_text = []
lines = f.readlines()
#%%%%%%%%%% TAKES ABOUT 2 MINUTES
for idx, line in enumerate(lines):
    wv_text.append(line.strip())

word_to_vec = {}

#%%%%%%%%%% TAKES ABOUT 4 MINUTES
for line in wv_text:
    parts = line.split()
    word = parts[0]
    vector = np.array([float(v) for v in parts[1:]])
    word_to_vec[word] = vector
f.close()
end = time.time()
print "Time Elapsed: {}".format(end - start)

Time Elapsed: 606.696414948


In [32]:
#-------------------------------------CNN-------------------------------------#
class CNN(nn.Module):
    def __init__(self, input_dim, hidden_dim):
        super(CNN, self).__init__()
        
        self.layer1 = nn.Sequential(
            nn.Conv1d(NUM_FEATURES_PER_WORD, hidden_dim, KERNEL_SIZE, padding = PADDING),
#             nn.ReLU()
            nn.Tanh()
        )
    def forward(self, x):
        x = self.layer1(x)
        return x

In [33]:
def create_data_loader(samples, shuffle_data = True, is_test_or_dev = False):
    features = []
    for sample in samples:
        target_title = sample[0]
        positive_title = sample[1]
        negative_titles = sample[2:]

        target_features = title_to_feature_matrix(target_title)
        positive_features = title_to_feature_matrix(positive_title)
        if len(negative_titles)==0:
            all_features=[target_features, positive_features]
        else:
            n_negative_features = [title_to_feature_matrix(negative_title) for negative_title in negative_titles]

            all_features = [target_features, positive_features] + n_negative_features
        #print all_features, "is all"
       # if is_test_or_dev:
       #     all_features = [target_features,]
        features.append(all_features)
        

    print(len(features), "is feature len")
    np_array=np.array(features)
    print (np_array.shape, "is features shape")
    targets = torch.LongTensor(len(features)).zero_()
    dataset = data_utils.TensorDataset(torch.FloatTensor(features), targets)
    data_loader = data_utils.DataLoader(dataset, batch_size = BATCH_SIZE, shuffle = shuffle_data)
    return data_loader

In [34]:
NUM_TRAINING_EXAMPLES=1000
NUM_FEATURES_PER_WORD=200
print "ok"
KERNEL_SIZE = 3 #MAKE SURE THIS NUMBER IS ODD SO THAT THE PADDING MAKES SENSE
PADDING = (KERNEL_SIZE - 1) / 2
INPUT_SIZE = NUM_FEATURES_PER_WORD
HIDDEN_SIZE = 600
LEARNING_RATE = 1e-4
MARGIN = 0.2
NUM_EPOCHS = 10
BATCH_SIZE = 50
print "hi"
NUM_BATCHES = NUM_TRAINING_EXAMPLES/BATCH_SIZE
PARAMETER_MAX_TITLE_LENGTH=38


ok
hi


In [35]:
def make_lookup_table(filename):
    lookup={}
    text_token_list=convert_to_list(filename)
    for token in text_token_list:
        lookup[token[0]] = {'title':token[1],'question':token[2]}
    return lookup

In [36]:
import random
def create_android_generated_samples(num_samples,text_token_list):
    print "done"
    samples = []
    for i in range(num_samples):
        id_num=text_token_list[i]
        #print id_num
        target_title = android_data_lookup_table[id_num[0]]['title']
        target_title = [item.lower() for item in target_title]
       #print target_title
        positive_title = generate_question(cfd, target_title)
        negative_ids = [text_token_list[random.randint(0,len(text_token_list)-1)] for j in range(20)]
        #print negative_ids
        negative_titles = [android_data_lookup_table[id_number[0]]['title'] for id_number in negative_ids]
        sample_to_add = [target_title]+[positive_title]+negative_titles
        print sample_to_add, "is sample"
        samples.append(sample_to_add)
    return samples

In [37]:
text_token_list=convert_to_list(android_text_tokenized_filename, is_android=True)

In [38]:
samples = create_android_generated_samples(5000, text_token_list)

done
[['i', "'ve", 'rooted', 'my', 'phone', '.', 'now', 'what', '?', 'what', 'do', 'i', 'gain', 'from', 'rooting', '?'], ['i', 'use', 'get', 'change', 'get', 'use', 'install', 'change', 'do', 'have', 'get', 'have', 'do', 'ca', 'change', 'have', 'change'], ['CM7', 'Launcherpro', 'Changing', 'Dock', 'Icons'], ['Installing', 'Google', 'apps', ';', '``', 'Google', 'Services', 'Framework', 'has', 'stopped', "''", 'after', 'installation'], ['just', 'boot', 'in', 'recovery', 'mode', 'htc', 'one', 'xl'], ['Android', 'update', 'not', 'proceeding', 'beyond', 'the', 'point', 'of', 'earlier', 'cancellation'], ['720p', 'or', '1080p', '-', 'How', 'to', 'verify', 'the', 'same', '?'], ['Update', 'ongoing', 'notification', 'stuck', 'after', 'reboot'], ['What', 'is', 'Plain', 'Vanilla', 'Android', '?'], ['Update', 'WebView', 'system', 'component', 'on', 'KitKat'], ['Could', "n't", 'communicate', 'with', 'Google', 'servers'], ['On', 'the', 'Galaxy', 'Tab', 'E', ',', 'when', 'you', 'open', 'an', 'applicat

[['how', 'do', 'i', 'properly', 'install', 'a', 'system', 'app', 'given', 'its', '.apk', '?'], ['how', 'long', 'can', 'does', 'long', 'does', 'is', 'long', 'can', 'is', 'is', 'does', 'to'], ['New', 'icons', 'do', 'not', 'display', 'consistently'], ['Unfortunately', ',', 'Music', 'has', 'stopped'], ['Recover', 'Pictures'], ['bug', 'with', 'nexus', '5', 'calendar'], ['how', 'to', 'run', 'a', 'specific', 'app', "'s", 'action', 'via', 'terminal', '?'], ['Swapping', 'External', 'to', 'Internal', 'Memory'], ['Installing', 'Jelly', 'Bean', 'on', 'Ice', 'Cream', 'Sandwich', 'tablet'], ['Incredible', '2', 'Sync', 'Problem'], ['Can', 'I', 'flash', 'CyanogenMod', 'without', 'unlocking', 'bootloader', '?'], ['How', 'can', 'I', 'manually', 'tilt', 'the', 'screen', 'when', 'auto', 'rotation', 'is', 'disabled', '?'], ['Join/Merge', 'external', 'SD', 'with', 'internal', 'SD', 'card', '?'], ['How', 'can', 'I', 'download', 'an', 'MP3', 'to', 'my', 'phone', 'instead', 'of', 'opening', 'it', 'in', 'a', 'm

[['where', 'to', 'find', 'an', 'original', 'android', 'image', '?'], ['where', 'does', 'does', 'can', 'are', 'did', 'do', 'is', 'does'], ['Samsung', 'Galaxy', 'S2', 'does', "n't", 'play', 'music'], ['XMBC', 'select', 'does', 'not', 'work', 'with', 'MK802III', 'and', 'Logitec', 'wireless', 'kb/mousepad', '-', 'how', 'to', 'resolve', '?'], ['How', 'Can', 'I', 'get', 'Google', 'Natives', 'apps', 'in', 'Samsung', 'Galaxy', 'S', '?'], ['Im', 'new', 'to', 'SetCPU', 'on', 'Moto', 'Droid', 'and', 'need', 'help'], ['Root', 'without', 'usb', '?'], ['Google', 'Calendar', 'gone', 'nuts', 'since', 'DST', 'has', 'ended'], ['Can', 'a', 'hybrid', 'install', 'be', 'converted', 'to', '``', 'internal', "''", '?'], ['Connecting', 'PS3', 'controller', 'to', 'Xperia', 'Z'], ['Error', 'while', 'running', 'debian', 'on', 'Arm6', 'based', 'phone'], ['Updating', 'any', 'app', 'is', 'retaining', 'its', 'older', 'version', '?'], ['HTTP', 'Progressive', 'Streaming', 'from', '.mp4', 'link', 'problem', 'in', 'Androi

[['does', 'access', 'to', 'logcat', 'need', 'root', '?'], ['does', "n't", 'my', 'the', 'my', "n't", 'it', 'android'], ['How', 'can', 'I', 'root', 'my', 'HTC', 'Incredible', 'S', '?'], ['My', 'storage', 'does', "n't", 'exist'], ['Installed', 'TWRP', ',', 'but', 'still', 'getting', 'Odin', '?'], ['Arabic', 'support', 'for', 'my', 'Android', 'device'], ['Odin', '4.38', 'not', 'detecting', 'my', 'GTS5570', '(', 'froyo', ')'], ['Ubuntu', 'font', 'can', 'not', 'display', 'latin', 'extended', 'characters'], ['change', 'native', 'Android', 'SIP', 'dialing', 'settings'], ['How', 'to', 'safely', 'unroot', 'my', 'Lenovo', 'K3', 'Note', '?'], ['My', 'user', 'data', 'wipes', 'after', 'every', 'boot', '!'], ['Which', 'one', 'to', 'install-', '32', 'bit', 'or', '64', 'bit', 'kernel', '?'], ['Which', 'A2SD', 'should', 'I', 'use', 'with', 'AOKP', 'VJ', '4.2.2', 'Jelly', 'Bean', 'v2.1', 'on', 'HTC', 'Desire'], ['Unable', 'to', 'play', 'Snapchat', 'videos'], ['WAP', 'Push', 'messages', '-', 'what', 'and'

[['how', 'to', 'make', 'certain', 'apps', 'turn', 'on', 'gps', 'automatically', '?'], ['how', 'is', 'does', 'do', 'can', 'is', 'long', 'do', 'can', 'is', 'long'], ['Install', 'apps', 'to', 'sd', 'card', 'by', 'default'], ['Google', 'Maps', 'constantly', 'requesting', 'location'], ['Smart', 'Lock', 'does', 'not', 'work', 'anymore'], ['HTC', 'Rhyme', '-', 'official', 'update'], ['Lenovo', 'tablet', 'with', 'two', 'internal', 'partitions', '-', 'How', 'to', 'move', 'apps', 'to', 'SD', '?'], ['Unable', 'to', 'reach', 'Google', 'Play', 'does', 'not', 'recognize', 'my', 'device'], ['launch/start', 'an', 'App', '(', 'Activity', ')', 'by', 'a', 'gesture', 'on', 'the', 'homescreen'], ['Regarding', 'file', 'association', 'in', 'ICS'], ['Samsung', 'Galaxy', 'S3', ':', 'can', 'not', 'sign', 'in', 'to', 'Play', 'Store'], ['How', 'to', 'remove', 'network', 'lock', 'samsung', 'galaxy', 's', 'advance'], ['Root', 'a', 'Moto', 'G', 'running', '4.4.4', 'KitKat'], ['problem', 'in', 'updating', 'CM12', 'ni

...

[['how', 'to', 'access', 'a', 'linux', 'shell', 'from', 'my', 'phone', 'via', 'bluetooth', '?'], ['how', 'do', 'is', 'can', 'is', 'can', 'does', 'much', 'long', 'long', 'is', 'does', 'to'], ['How', 'to', 'go', 'change', 'azerty', 'to', 'qwerty', 'on', 'huawei', 'ascend', 'y530'], ['Why', 'do', 'apps', 'legitimately', 'purchased', 'from', 'Android', 'Market', 'warn', 'about', 'missing', 'license', '?'], ['How', 'Google', 'can', 'check', 'whether', 'an', 'application', 'is', 'installed', 'from', 'Play', 'Store', 'or', 'Not', '?'], ['Are', 'IPv6', 'Privacy', 'Extensions', 'supported', 'and', 'how', 'can', 'they', 'be', 'enabled/disabled', '?'], ['Can', 'not', 'enter', 'fastboot', 'mode', 'after', 'flashing', 'custom', 'recovery'], ['Problem', 'of', 'lack', 'of', 'storage', 'space', 'in', 'the', 'system', 'storage'], ['Google', 'Glass', 'Stuck', 'at', 'the', 'Glass', 'screen'], ['Where', 'are', 'the', 'sources', 'and', 'issue', 'tracker', 'of', 'Ghandicam', '?'], ['Fairphone', 'Open', 'stu

[['ubuntu', 'one', 'app', ':', 'how', 'can', 'i', 'sync', 'a', 'text', 'file', 'edited', 'on', 'my', 'android', 'device', 'with', 'ubuntu', 'one', '?'], ['ubuntu', '12.04', 'for', 'on', '?', '12.04', 'to', 'on', 'to', 'on', 'desktop', '?', '?', 'to', '?', 'to', 'desktop', '?', '12.04', 'to', '?'], ['Is', 'it', 'possible', 'to', 'flash', 'CM', 'for', 'Samsung', 'S3', 'I9300', 'on', 'different', 'version', '?'], ['Handling', 'Notifications', '-', 'Vibrations', '/', 'Screen', '/', 'Tones', '?'], ['Android', 'wo', "n't", 'boot', 'even', 'after', 'flashing', 'stock', 'ROM'], ['Joining', 'a', 'public', 'WiFi', 'made', 'the', 'owner', 'able', 'to', 'send', 'me', 'a', 'Facebook', 'friend', 'request', '.', 'How', '?'], ['Play', 'Store', 'Downloading', 'of', 'Updates', 'Stuck', 'part', 'way', 'through', 'download'], ['``', 'Android', 'is', 'upgrading', '...', 'Starting', 'Apps', "''", 'on', 'boot'], ['How', 'do', 'I', 'remove', 'the', 'screen', 'lock', 'that', 'I', 'placed', 'on', 'my', 'device'

[['how', 'can', 'i', 'install', 'vanilla', 'android', 'on', 'the', 'kindle', 'fire', '?'], ['how', 'long', 'is', 'is', 'to', 'does', 'do', 'is', 'can', 'do', 'do', 'much'], ['Installing', 'Android', 'apps', 'from', 'Samsung', 'store', 'to', 'non', 'Samsung', 'Android', 'device', 'like', 'htc', 'phone'], ['How', 'to', 'get', 'mobile', 'site', 'in', 'Firefox', 'to', 'be', 'displayed', 'as', 'in', 'Chrome', 'for', 'Android', 'if', 'spoofing', 'does', "n't", 'help', '?'], ['Bluetooth', 'Tethering', 'on', 'Galaxy', 'S4'], ['Can', 'I', 'connect', 'a', 'pendrive', 'to', 'samsung', 'galaxy', 'core', '?'], ['Installing', 'applications', 'with', 'larger', 'size', 'on', 'S', 'DUOS'], ['Enabling', 'developer', 'mode', 'in', 'Huawei', 'Mediapad', 'M2', '10.0'], ['Phone', 'changes', 'timezone', 'itself'], ['I', 'ca', "n't", 'install', 'any', 'app', 'that', 'requires', 'at', 'least', 'Android', '5.0', 'although', 'I', "'ve", 'updated', 'to', '5.0'], ['Phone', 'connected', 'to', 'wireless', 'but', 'do

[['how', 'can', 'i', 'prevent', 'the', 'google+', 'app', 'from', 'showing', 'the', 'wrong', 'thumbnail', 'before', 'i', 'share', 'a', 'photo', '?'], ['how', 'to', 'much', 'long', 'can', 'do', 'can', 'to', 'to', 'can', 'do', 'is', 'to', 'is', 'much', 'much', 'much', 'does', 'does'], ['Why', 'choice', 'of', 'dvm', 'is', 'obvious', 'for', 'android', 'why', 'not', 'use', 'jvm', '?'], ['ROOTING', 'THE', 'ANDROID', 'DEVICE'], ['Quickest', 'way', 'to', 'toggle', 'between', 'apps', '(', 'Alt-Tab', 'equivalent', ')', '*not*', 'requiring', '3rd-party', 'apps', '?'], ['Do', 'I', 'root', 'to', 'my', 'model', ',', 'or', 'my', 'version', 'number', '?'], ['Status', 'of', 'a', 'recently', 'added', 'contact'], ['Determine', 'strength', 'of', 'the', 'cell', 'antenna', 'in', 'an', 'Android', 'phone', 'to', 'ensure', 'good', 'cell', 'reception'], ['What', "'s", 'the', 'easiest', 'way', 'to', 'sync', 'music', 'to', 'my', 'phone', '?'], ['Setting', 'IncognitoModeAvailability', 'policy', 'for', 'Google', 'Ch

[['how', 'can', 'i', 'purchase', 'apps', 'from', 'the', 'amazon', 'appstore', 'without', 'downloading', 'them', '?'], ['how', 'much', 'is', 'much', 'does', 'much', 'long', 'can', 'long', 'much', 'do', 'can', 'do', 'do'], ['Default', 'music', 'player', 'restarting', 'song', 'on', 'Bluetooth', 'reconnect'], ['Normal', 'calls', 'are', 'restricted', 'by', 'access', 'control', '--', 'blocking', 'incoming', 'and', 'outgoing', 'calls'], ['Complete', 'Dropbox', 'implementation', 'for', 'Android'], ['Why', 'wo', "n't", 'badge', 'notification', 'work', 'for', 'Gmail', 'on', 'my', 'S3', '?'], ['How', 'do', 'I', 'set', 'reminders', 'using', 'Voice', 'Actions', 'in', 'ICS', '4', '-', 'Galaxy', 'Nexus', '?'], ['Google', 'Play', 'website', 'says', 'I', 'have', 'certain', 'apps', 'installed', 'that', 'I', 'do', 'not', '.', 'How', 'to', 're-sync', '?'], ['What', 'are', 'some', 'of', 'the', 'effects', 'of', 'flashing', 'my', 'HTC', 'Desire', 'with', 'cyanogenmod', '?'], ['change', 'UI', 'dynamically', '

In [39]:
final_train_data_loader=create_data_loader(samples)

(5000, 'is feature len')
((5000, 22), 'is features shape')


RuntimeError: inconsistent sequence length at index (0, 0, 16, 299) - expected 300 but got 200

In [ ]:
cos = nn.CosineSimilarity(dim=1, eps=1e-6)


def evaluate_model_on_test(model, test_data_filename):
    test_data_loader =convert_to_list(test_data_filename)
    
    model.eval() #change model to 'eval' mode
    correct = 0
    total = 0
    p5 = 0
    MRR = 0
    all_data = []
    for sample in test_data_loader:
        #print sample
        target_id=sample[0]
        similar_ids=sample[1]
        #print similar_ids, 'similar'
        candidate_ids=sample[2]
        #print candidate_ids, 'candidates'
        titles = convert_sampleids_to_titles([sample], lookup,is_dev_or_test=True)[0]

        #print titles
        twenty_one_features = [title_to_feature_matrix(title) for title in titles]
        
        cosine_sims = sample_to_cosine_sims(twenty_one_features, model = model)
        #print cosine_sims
        #_, predicted = torch.max(cosine_sims, 0)
       # total += label.size(0)
       # label = label.squeeze()
        
        #correct += ((predicted == label).sum().data.numpy().squeeze())
        cosine_sims = [cos_sim.data.numpy()[0] for cos_sim in cosine_sims]
        #cosine_sims = cosine_sims.data.numpy().T
        #print cosine_sims, "is cos sims"
        #print candidate_ids, 'is candidates'
        gold_labels = [1 if identity in similar_ids else 0 for identity in candidate_ids]
        #print gold_labels, "is gold"
        
        index_order = sorted(range(len(cosine_sims)), reverse = True,key=lambda k: cosine_sims[k])
        #print index_order, "is index order"
        
        data = [gold_labels[index] for index in index_order]
        all_data.append(data)
#         for instance_idx in range(len(cosine_sims)):
#             cosine_sims_at_idx = cosine_sims[instance_idx]            
#             print "Cosine sims at idx: {}".format(cosine_sims_at_idx)
#             a
#             loc = np.squeeze(np.where(cosine_sims_at_idx.argsort()[::-1] == 0))
#             data_instance = [0] * len(cosine_sims_at_idx)
#             data_instance[loc] = 1
#             data.append(data_instance)
        
#         for instance_idx in range(len(cosine_sims)):
#             cosine_sims_at_idx = cosine_sims[instance_idx]
#             top_5_indices = cosine_sims_at_idx.argsort()[-5:][::-1]
#             label_at_idx = 0
#             if label_at_idx in top_5_indices:
#                 p5 += 1
            
#             MRR += 1. / (1. + np.squeeze(np.where(cosine_sims_at_idx.argsort()[::-1] == 0)))
    return all_data 

def sample_to_cosine_sims(sample, model = None):
    #RE-ORDER DIMENSIONS OF THE SAMPLE
    sample = Variable(torch.FloatTensor(sample))
    #print sample.unsqueeze(0)
    # 1x21x200x38
    sample = sample.unsqueeze(0).permute(1, 0, 2, 3)
    if model != None:
        net = model
    #21 x 1 x 200 x 38
    target_question_features = sample[0] # 1 x 1 x 200 x 38
   # print target_question_features.data.numpy()shape, 'Is target"'
    other_question_features = sample[1:] # 20 x 1 x 200 x 38
   # print other_question_features.data.numpy()shape, "is other"

    #Determine lengths to know how many vectors to take the average across.
    target_question_lengths = find_start_of_padding_for_batch(target_question_features.data)
    other_questions_lengths = [find_start_of_padding_for_batch(negative.data) for negative in other_question_features]

    #RUN THROUGH NET
    target_question_net_output = net(target_question_features)
    other_question_net_outputs = [net(negative) for negative in other_question_features]

    #CREATE MASKS
    target_questions_masks = [create_mask(_) for _ in target_question_lengths] #DIM = 50 x 100 x 38
    other_questions_masks = [[create_mask(length) for length in length_list] #DIM = 50 x 20 x 100 x 38
                                  for length_list in other_questions_lengths]

    #APPLY MASKS
    #Should the multiplicands, the masks, be Float Tensors or Variables? May have to be float tensors to ensure
    #    pytorch's directed graph back-prop is maintained.

    target_question_net_output_masked = target_question_net_output * Variable(torch.FloatTensor(target_questions_masks))
    other_questions_net_output_masked = [other_question_net_outputs[idx] * 
                                              Variable(torch.FloatTensor(other_questions_masks[idx]))
                                              for idx in range(20)]

    #SUM OVER WORDS
    target_question_net_output_masked_summed = torch.sum(target_question_net_output_masked, dim = 2) #DIM = 50 x 100
    other_questions_net_output_masked_summed = [torch.sum(
                                                    other_questions_net_output_masked[idx], dim = 2
                                                    )for idx in range(20)] #DIM = 20 x 50 x 100


    #cosine_similarity_pos = cos(target_question_net_output_masked_summed, positive_question_net_output_masked_summed)
    # ^ DIM = 50
    cosine_similarities = [cos(target_question_net_output_masked_summed, other_questions_net_output_masked_summed[idx])
                              for idx in range(20)]
    # ^ DIM = 20 x 50
    #

    #cosine_similarities = torch.stack([cosine_similarity_pos] + cosine_similarities_neg) # DIM = 21 x 50
    return cosine_similarities


In [ ]:
def create_data_loader_test(android_samples, shuffle_data = True):
    features = []

    for sample in android_samples:
        target_title = sample[0]
        positive_title = sample[1]
        negative_titles = sample[2:22] #:22 because there are more negatives in the android dataset, but a TA
                                       # said the extras aren't necessary

        target_features = title_to_feature_matrix(target_title)
        positive_features = title_to_feature_matrix(positive_title)
        n_negative_features = [title_to_feature_matrix(negative_title) for negative_title in negative_titles]

        all_features = [target_features, positive_features] + n_negative_features

        features.append(all_features)
        
    return features

In [ ]:

'''
Code took from PyTorchNet (https://github.com/pytorch/tnt)

'''

import math
import numbers
import numpy as np
import torch

class Meter(object):
    def reset(self):
        pass

    def add(self):
        pass

    def value(self):
        pass


class AUCMeter(Meter):
    """
    The AUCMeter measures the area under the receiver-operating characteristic
    (ROC) curve for binary classification problems. The area under the curve (AUC)
    can be interpreted as the probability that, given a randomly selected positive
    example and a randomly selected negative example, the positive example is
    assigned a higher score by the classification model than the negative example.

    The AUCMeter is designed to operate on one-dimensional Tensors `output`
    and `target`, where (1) the `output` contains model output scores that ought to
    be higher when the model is more convinced that the example should be positively
    labeled, and smaller when the model believes the example should be negatively
    labeled (for instance, the output of a signoid function); and (2) the `target`
    contains only values 0 (for negative examples) and 1 (for positive examples).
    """
    def __init__(self):
        super(AUCMeter, self).__init__()
        self.reset()

    def reset(self):
        # self.scores = torch.DoubleTensor(torch.DoubleStorage()).numpy()
        # self.targets = torch.LongTensor(torch.LongStorage()).numpy()
        self.scores = []
        self.targets = []

    def add(self, output, target):
        if torch.is_tensor(output):
            output = output.cpu().squeeze().numpy()
        if torch.is_tensor(target):
            target = target.cpu().squeeze().numpy()
        # elif isinstance(target, numbers.Number):
        #     target = np.asarray([target])
        # assert np.ndim(output) == 1, \
        #     'wrong output size (1D expected)'
        # assert np.ndim(target) == 1, \
        #     'wrong target size (1D expected)'
        # assert output.shape[0] == target.shape[0], \
        #     'number of outputs and targets does not match'
        # assert np.all(np.add(np.equal(target, 1), np.equal(target, 0))), \
        #     'targets should be binary (0, 1)'

        # self.scores = np.append(self.scores, output)
        # self.targets = np.append(self.targets, target)
        self.sortind = None
        self.scores.append(output)
        self.scores.append(target)


    def value(self, max_fpr=1.0):
#         self.scores = torch.FloatTensor(self.scores)
#         self.target = torch.LongTensor(self.targets)
        
        assert max_fpr > 0

        # case when number of elements added are 0
#         if self.scores.shape[0] == 0:
#             return 0.5

        # sorting the arrays
        if self.sortind is None:
            scores, sortind = torch.sort(torch.from_numpy(self.scores), dim=0, descending=True)
            scores = scores.numpy()
            self.sortind = sortind.numpy()
        else:
            scores, sortind = self.scores, self.sortind

        # creating the roc curve
        tpr = np.zeros(shape=(scores.size + 1), dtype=np.float64)
        fpr = np.zeros(shape=(scores.size + 1), dtype=np.float64)

        for i in range(1, scores.size + 1):
            if self.targets[sortind[i - 1]] == 1:
                tpr[i] = tpr[i - 1] + 1
                fpr[i] = fpr[i - 1]
            else:
                tpr[i] = tpr[i - 1]
                fpr[i] = fpr[i - 1] + 1

        tpr /= (self.targets.sum() * 1.0)
        fpr /= ((self.targets - 1.0).sum() * -1.0)

        for n in range(1, scores.size + 1):
            if fpr[n] >= max_fpr:
                break

        # calculating area under curve using trapezoidal rule
        #n = tpr.shape[0]
        h = fpr[1:n] - fpr[0:n - 1]
        sum_h = np.zeros(fpr.shape)
        sum_h[0:n - 1] = h
        sum_h[1:n] += h
        area = (sum_h * tpr).sum() / 2.0

        return area / max_fpr

In [ ]:
MAX_TITLE_LENGTH=38
INPUT_DIM = (MAX_TITLE_LENGTH, NUM_FEATURES_PER_WORD)
net = CNN(INPUT_SIZE, HIDDEN_SIZE)
#net=torch.load("Net_Epoch_8")
criterion = nn.MultiMarginLoss(p=1, margin=MARGIN, weight = None, size_average=True) #HAHA just put these in to look smart 
optimizer = torch.optim.Adam(net.parameters(), lr = LEARNING_RATE)

cos = nn.CosineSimilarity(dim=1, eps=1e-6)
print "Beginning training..."
# ----TRAINING
for epoch in range(NUM_EPOCHS):
    running_loss = 0.0
    for idx,(sample, label) in enumerate(final_train_data_loader):
        print idx,
#     for idx in range(NUM_BATCHES):
        #Sample shape: [50, 22, 200, 38]
        #50 - Batch size, 22 - Num questions per data point
        sample = Variable(sample, requires_grad = True)
        label = Variable(label, requires_grad = True)

        #RE-ORDER DIMENSIONS OF THE SAMPLE
        sample = sample.permute(1, 0, 2, 3)
        
        target_question_features = sample[0] # 50 x 200 x 38
        positive_question_features = sample[1] # 50 x 200 x 38
        N_negative_question_features = sample[2:] #20 x 50 x 200 x 38
        
        #Determine lengths to know how many vectors to take the average across.
        target_question_lengths = find_start_of_padding_for_batch(target_question_features.data)
        positive_question_lengths = find_start_of_padding_for_batch(positive_question_features.data)
        N_negative_questions_lengths = [find_start_of_padding_for_batch(negative.data) for negative in N_negative_question_features]
        
        #RUN THROUGH NET
        target_question_net_output = net(target_question_features)
        positive_question_net_output = net(positive_question_features)
        N_negative_question_net_outputs = [net(negative) for negative in N_negative_question_features]
        
        #CREATE MASKS
        target_questions_masks = [create_mask(_) for _ in target_question_lengths] #DIM = 50 x 100 x 38
        positive_questions_masks = [create_mask(_) for _ in positive_question_lengths] #DIM = 50 x 100 x 38
        N_negative_questions_masks = [[create_mask(length) for length in length_list] #DIM = 50 x 20 x 100 x 38
                                      for length_list in N_negative_questions_lengths]
        
        #APPLY MASKS
        #Should the multiplicands, the masks, be Float Tensors or Variables? May have to be float tensors to ensure
        #    pytorch's directed graph back-prop is maintained.

        target_question_net_output_masked = target_question_net_output * Variable(torch.FloatTensor(target_questions_masks))
        positive_question_net_output_masked = positive_question_net_output * Variable(torch.FloatTensor(positive_questions_masks))
        N_negative_questions_net_output_masked = [N_negative_question_net_outputs[idx] * 
                                                  Variable(torch.FloatTensor(N_negative_questions_masks[idx]))
                                                  for idx in range(NUM_NEGATIVE_SAMPLES)]

        #SUM OVER WORDS
        target_question_net_output_masked_summed = torch.sum(target_question_net_output_masked, dim = 2) #DIM = 50 x 100
        positive_question_net_output_masked_summed = torch.sum(positive_question_net_output_masked, dim = 2) #DIM = 50 x 100
        N_negative_questions_net_output_masked_summed = [torch.sum(
                                                        N_negative_questions_net_output_masked[idx], dim = 2
                                                        )for idx in range(NUM_NEGATIVE_SAMPLES)] #DIM = 20 x 50 x 100

        
        cosine_similarity_pos = cos(target_question_net_output_masked_summed, positive_question_net_output_masked_summed)
        # ^ DIM = 50
        cosine_similarities_neg = [cos(target_question_net_output_masked_summed, N_negative_questions_net_output_masked_summed[idx])
                                  for idx in range(NUM_NEGATIVE_SAMPLES)]
        # ^ DIM = 20 x 50
        #

        cosine_similarities = torch.stack([cosine_similarity_pos] + cosine_similarities_neg) # DIM = 21 x 50
        
        optimizer.zero_grad()
        
        cosine_similarities = torch.t(cosine_similarities)
        label = torch.squeeze(label)
        loss = criterion(cosine_similarities, label)
        
        loss.backward()
        
        running_loss += loss.data[0]
        
        optimizer.step()
        
    torch.save(net, "feature_extract_generator_{}".format(epoch))
    print ""
    print "Loss after epoch " + str(epoch) + " :" + str(running_loss)

In [ ]:
def sample_and_label_to_cosine_sims(sample, label, model = None):
    #RE-ORDER DIMENSIONS OF THE SAMPLE
    sample = sample.permute(1, 0, 2, 3)
    if model != None:
        net = model
    
    target_question_features = sample[0] # 50 x 200 x 38
    positive_question_features = sample[1] # 50 x 200 x 38
    N_negative_question_features = sample[2:] #20 x 50 x 200 x 38

    #Determine lengths to know how many vectors to take the average across.
    target_question_lengths = find_start_of_padding_for_batch(target_question_features.data)
    positive_question_lengths = find_start_of_padding_for_batch(positive_question_features.data)
    N_negative_questions_lengths = [find_start_of_padding_for_batch(negative.data) for negative in N_negative_question_features]

    #RUN THROUGH NET
    target_question_net_output = net(target_question_features)
    positive_question_net_output = net(positive_question_features)
    N_negative_question_net_outputs = [net(negative) for negative in N_negative_question_features]

    #CREATE MASKS
    target_questions_masks = [create_mask(_) for _ in target_question_lengths] #DIM = 50 x 100 x 38
    positive_questions_masks = [create_mask(_) for _ in positive_question_lengths] #DIM = 50 x 100 x 38
    N_negative_questions_masks = [[create_mask(length) for length in length_list] #DIM = 50 x 20 x 100 x 38
                                  for length_list in N_negative_questions_lengths]

    #APPLY MASKS
    #Should the multiplicands, the masks, be Float Tensors or Variables? May have to be float tensors to ensure
    #    pytorch's directed graph back-prop is maintained.

    target_question_net_output_masked = target_question_net_output * Variable(torch.FloatTensor(target_questions_masks))
    positive_question_net_output_masked = positive_question_net_output * Variable(torch.FloatTensor(positive_questions_masks))
    N_negative_questions_net_output_masked = [N_negative_question_net_outputs[idx] * 
                                              Variable(torch.FloatTensor(N_negative_questions_masks[idx]))
                                              for idx in range(NUM_NEGATIVE_SAMPLES)]
    #SUM OVER WORDS
    target_question_net_output_masked_summed = torch.sum(target_question_net_output_masked, dim = 2) #DIM = 50 x 100
    positive_question_net_output_masked_summed = torch.sum(positive_question_net_output_masked, dim = 2) #DIM = 50 x 100
    N_negative_questions_net_output_masked_summed = [torch.sum(
                                                    N_negative_questions_net_output_masked[idx], dim = 2
                                                    )for idx in range(NUM_NEGATIVE_SAMPLES)] #DIM = 20 x 50 x 100

    net_outputs_batch = torch.stack([target_question_net_output_masked_summed, positive_question_net_output_masked_summed] + N_negative_questions_net_output_masked_summed)
    
    cosine_similarity_pos = cos(target_question_net_output_masked_summed, positive_question_net_output_masked_summed)
    # ^ DIM = 50
    cosine_similarities_neg = [cos(target_question_net_output_masked_summed, N_negative_questions_net_output_masked_summed[idx])
                              for idx in range(NUM_NEGATIVE_SAMPLES)]
    # ^ DIM = 20 x 50
    #

    cosine_similarities = torch.stack([cosine_similarity_pos] + cosine_similarities_neg) # DIM = 21 x 50
    return cosine_similarities, net_outputs_batch

def mse_loss(input, target):
    return torch.sum((input - target) ** 2) / input.data.nelement()


In [ ]:
auc_evaluator = AUCMeter()
feature_extractor_test = torch.load("feature_extract_generator_0")
correct = 0.
total = 0.
outputs = []
targets = []
test_features = create_data_loader_test(android_test_titles_only)

for feature in test_features:
    feature = Variable(torch.FloatTensor(feature))
    feature = feature.unsqueeze(0)
    labels = Variable(torch.LongTensor([1] + [0] * 20))
    cosine_sims, _ = sample_and_label_to_cosine_sims(feature, labels, model = feature_extractor_test)
    if (np.argmax(cosine_sims.data.numpy()) == 0):
        correct += 1
    total += 1
    for idx in range(len(cosine_sims)):
        output = cosine_sims[idx].data.numpy()[0]
        label = labels[idx].data.numpy()[0]
#         auc_evaluator.add(output, label)
        outputs.append(output)
        targets.append(label)
auc_evaluator.scores = np.array(outputs)
auc_evaluator.targets = np.array(targets)
auc_evaluator.sortind = None
print "AUC Value (0.05): {}".format(auc_evaluator.value(0.05))
print "Accuracy: {}".format(correct/total)